<a href="https://colab.research.google.com/github/WallaceRFernandes/CodigosONG_SMA/blob/main/SendpulseDados.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#installs e libs
!pip install pysendpulse
!pip install IPython
!pip install pandas
from pysendpulse.pysendpulse import PySendPulse
from IPython.display import display
from pandas import json_normalize
import collections
import datetime
import requests
import base64
import json
import pandas as pd

  Preparing metadata (setup.py) ... done
  Created wheel for python3-memcached: filename=python3_memcached-1.51-py3-none-any.whl size=14382 sha256=273ad9be3538435ce3d988e6b360e1ddbabfdfb09435f95df8a408202adba455
  Stored in directory: /root/.cache/pip/wheels/50/02/82/7d651cbabbea97f8214de366974ca37cf7dc8c490d6d2235dd
Successfully built python3-memcached
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 58.8 MB/s eta 0:00:00


In [ ]:
url = "https://api.sendpulse.com/oauth/access_token"

payload = {
    "grant_type": "client_credentials",
    "client_id": "",
    "client_secret": ""
}

response = requests.post(url, json=payload)


access_token = json.loads(response.text)['access_token']


headers = {
    'Authorization': f'Bearer {access_token}'
}

In [ ]:
sms_campanhas = requests.get('https://api.sendpulse.com/sms/campaigns/list', headers=headers)
sms_campanhas.json()
print(sms_campanhas.json())

{'result': True, 'data': [{'id': 29351, 'address_book_id': 0, 'company_price': '1.12000', 'company_currency': 'BRL', 'send_date': '2021-11-17 13:31:22', 'date_created': '2021-11-17 13:31:22', 'sender_name': 'Ong BdM'}, {'id': 29382, 'address_book_id': 0, 'company_price': '135.24000', 'company_currency': 'BRL', 'send_date': '2021-11-17 13:46:19', 'date_created': '2021-11-17 13:46:20', 'sender_name': 'Ong BdM'}, {'id': 29388, 'address_book_id': 0, 'company_price': '69.16000', 'company_currency': 'BRL', 'send_date': '2021-11-17 13:48:49', 'date_created': '2021-11-17 13:48:49', 'sender_name': 'Ong BdM'}, {'id': 66958, 'address_book_id': 0, 'company_price': '75.39000', 'company_currency': 'BRL', 'send_date': '2021-12-08 14:26:01', 'date_created': '2021-12-08 14:26:02', 'sender_name': 'Ong BdM'}, {'id': 66962, 'address_book_id': 0, 'company_price': '105.00000', 'company_currency': 'BRL', 'send_date': '2021-12-08 14:28:27', 'date_created': '2021-12-08 14:28:29', 'sender_name': 'Ong BdM'}, {'i

In [ ]:
df_sms = pd.DataFrame(sms_campanhas.json())
df_sms.to_csv('df_sms.csv', index=False)

In [ ]:
df_sms_expandido = json_normalize(df_sms['data']) # Expande a coluna 'data'

df_sms_desaninhado = pd.concat([df_sms, df_sms_expandido], axis=1) # Concatena os DataFrames

df_sms_desaninhado = df_sms_desaninhado.drop(['data'], axis=1)

print(df_sms_desaninhado)

     result       id  address_book_id company_price company_currency  \
0      True    29351                0       1.12000              BRL   
1      True    29382                0     135.24000              BRL   
2      True    29388                0      69.16000              BRL   
3      True    66958                0      75.39000              BRL   
4      True    66962                0     105.00000              BRL   
..      ...      ...              ...           ...              ...   
223    True  3477865                0       0.08000              BRL   
224    True  3477866                0       0.08000              BRL   
225    True  3477868                0       0.08000              BRL   
226    True  3477871                0       0.08000              BRL   
227    True  3477874                0       0.11000              BRL   

               send_date         date_created sender_name  
0    2021-11-17 13:31:22  2021-11-17 13:31:22     Ong BdM  
1    2021-11-17

In [ ]:
df_sms_desaninhado.to_csv('df_sms_desaninhado.csv', index=False)

In [ ]:
ids = df_sms_desaninhado['id'].tolist()

# Cria uma lista para armazenar os dados de cada campanha
campaign_data = []

# Loop através de cada ID
for id in ids:
    # Constrói a URL com o ID atual
    url = f'https://api.sendpulse.com/sms/campaigns/info/{id}'

    # Faz a requisição GET
    response = requests.get(url, headers=headers)

    # Verifica se a requisição foi bem-sucedida
    if response.status_code == 200:
        # Adiciona os dados da campanha à lista
        campaign_data.append(response.json())

# Cria um novo DataFrame com os dados das campanhas
df_campaigns = pd.DataFrame(campaign_data)

In [ ]:
print(campaign_data)

[{'result': True, 'data': {'id': 29351, 'address_book_id': 0, 'currency': 'BRL', 'company_price': '1.12000', 'send_date': '2021-11-17 13:31:22', 'date_created': '2021-11-17 13:31:22', 'sender_name': 'Ong BdM', 'task_phones_info': [{'phone': 5511959803214, 'status': 2, 'status_explain': 'Delivered', 'country_code': 'BR', 'money_spent': 0.07}, {'phone': 5511967139993, 'status': 2, 'status_explain': 'Delivered', 'country_code': 'BR', 'money_spent': 0.07}, {'phone': 5511978171946, 'status': 2, 'status_explain': 'Delivered', 'country_code': 'BR', 'money_spent': 0.07}, {'phone': 5511991463737, 'status': 2, 'status_explain': 'Delivered', 'country_code': 'BR', 'money_spent': 0.07}]}}, {'result': True, 'data': {'id': 29382, 'address_book_id': 0, 'currency': 'BRL', 'company_price': '135.24000', 'send_date': '2021-11-17 13:46:19', 'date_created': '2021-11-17 13:46:20', 'sender_name': 'Ong BdM', 'task_phones_info': [{'phone': 551194603981, 'status': 2, 'status_explain': 'Delivered', 'country_code'

In [ ]:
df_campaigns.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   result  228 non-null    bool  
 1   data    228 non-null    object
dtypes: bool(1), object(1)
memory usage: 2.1+ KB


In [ ]:
df_info_campanhas = json_normalize(df_campaigns['data'])

df_info_campanhas = pd.concat([df_campaigns, df_info_campanhas], axis=1)

df_info_campanhas = df_info_campanhas.drop(['data'], axis=1)

In [ ]:
df_info_campanhas.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 9 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   result            228 non-null    bool  
 1   id                228 non-null    int64 
 2   address_book_id   228 non-null    int64 
 3   currency          228 non-null    object
 4   company_price     228 non-null    object
 5   send_date         228 non-null    object
 6   date_created      228 non-null    object
 7   sender_name       228 non-null    object
 8   task_phones_info  228 non-null    object
dtypes: bool(1), int64(2), object(6)
memory usage: 14.6+ KB


In [ ]:
df_info_campanhas['task_phones_info_count'] = df_info_campanhas['task_phones_info'].apply(len)

In [ ]:
df_info_campanhas.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 10 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   result                  228 non-null    bool  
 1   id                      228 non-null    int64 
 2   address_book_id         228 non-null    int64 
 3   currency                228 non-null    object
 4   company_price           228 non-null    object
 5   send_date               228 non-null    object
 6   date_created            228 non-null    object
 7   sender_name             228 non-null    object
 8   task_phones_info        228 non-null    object
 9   task_phones_info_count  228 non-null    int64 
dtypes: bool(1), int64(3), object(6)
memory usage: 16.4+ KB


In [ ]:
display(df_info_campanhas)

result       id  address_book_id currency company_price  \
0      True    29351                0      BRL       1.12000   
1      True    29382                0      BRL     135.24000   
2      True    29388                0      BRL      69.16000   
3      True    66958                0      BRL      75.39000   
4      True    66962                0      BRL     105.00000   
..      ...      ...              ...      ...           ...   
223    True  3477865                0      BRL       0.08000   
224    True  3477866                0      BRL       0.08000   
225    True  3477868                0      BRL       0.08000   
226    True  3477871                0      BRL       0.08000   
227    True  3477874                0      BRL       0.11000   

               send_date         date_created sender_name  \
0    2021-11-17 13:31:22  2021-11-17 13:31:22     Ong BdM   
1    2021-11-17 13:46:19  2021-11-17 13:46:20     Ong BdM   
2    2021-11-17 13:48:49  2021-11-17 13:48:49     Ong BdM   
3    2021-12-08 14:26:01  2021-12-08 14:26:02     Ong BdM   
4    2021-12-08 14:28:27  2021-12-08 14:28:29     Ong BdM   
..                   ...                  ...         ...   
223  2024-10-03 20:57:05  2024-10-03 20:57:05     Somando   
224  2024-10-03 21:00:31  2024-10-03 21:00:31     Somando   
225  2024-10-03 21:11:07  2024-10-03 21:11:07     Somando   
226  2024-10-03 21:27:18  2024-10-03 21:27:18     Somando   
227  2024-10-03 21:31:30  2024-10-03 21:31:30     Somando   

                                      task_phones_info  task_phones_info_count  
0    [{'phone': 5511959803214, 'status': 2, 'status...                       4  
1    [{'phone': 551194603981, 'status': 2, 'status_...                     483  
2    [{'phone': 551195332832, 'status': 2, 'status_...                     247  
3    [{'phone': 551194603981, 'status': 2, 'status_...                     359  
4    [{'phone': 551195332832, 'status': 2, 'status_...                     500  
..                                                 ...                     ...  
223  [{'phone': 5515992618875, 'status': 0, 'status...                       1  
224  [{'phone': 5515992618875, 'status': 12, 'statu...                       1  
225  [{'phone': 5515992618875, 'status': 0, 'status...                       1  
226  [{'phone': 5515992618875, 'status': 0, 'status...                       1  
227  [{'phone': 15992618875, 'status': 0, 'status_e...                       1  

[228 rows x 10 columns]

In [ ]:
def count_explains(events):
  explain_counts = collections.Counter()
  for event in events:
    explain = event.get('status_explain')
    if explain:
      explain_counts[explain] += 1
  return explain_counts

df_info_campanhas['explain_counts'] = df_info_campanhas['task_phones_info'].apply(count_explains)

for explain in df_info_campanhas['explain_counts'].apply(lambda x: x.keys()).explode().unique():
  df_info_campanhas[f'count_{explain}'] = df_info_campanhas['explain_counts'].apply(lambda x: x.get(explain, 0))

# Remover a coluna 'explain_counts' (opcional)
df_info_campanhas_contagem = df_info_campanhas.drop('explain_counts', axis=1)

display(df_info_campanhas_contagem)

result       id  address_book_id currency company_price  \
0      True    29351                0      BRL       1.12000   
1      True    29382                0      BRL     135.24000   
2      True    29388                0      BRL      69.16000   
3      True    66958                0      BRL      75.39000   
4      True    66962                0      BRL     105.00000   
..      ...      ...              ...      ...           ...   
223    True  3477865                0      BRL       0.08000   
224    True  3477866                0      BRL       0.08000   
225    True  3477868                0      BRL       0.08000   
226    True  3477871                0      BRL       0.08000   
227    True  3477874                0      BRL       0.11000   

               send_date         date_created sender_name  \
0    2021-11-17 13:31:22  2021-11-17 13:31:22     Ong BdM   
1    2021-11-17 13:46:19  2021-11-17 13:46:20     Ong BdM   
2    2021-11-17 13:48:49  2021-11-17 13:48:49     Ong BdM   
3    2021-12-08 14:26:01  2021-12-08 14:26:02     Ong BdM   
4    2021-12-08 14:28:27  2021-12-08 14:28:29     Ong BdM   
..                   ...                  ...         ...   
223  2024-10-03 20:57:05  2024-10-03 20:57:05     Somando   
224  2024-10-03 21:00:31  2024-10-03 21:00:31     Somando   
225  2024-10-03 21:11:07  2024-10-03 21:11:07     Somando   
226  2024-10-03 21:27:18  2024-10-03 21:27:18     Somando   
227  2024-10-03 21:31:30  2024-10-03 21:31:30     Somando   

                                      task_phones_info  \
0    [{'phone': 5511959803214, 'status': 2, 'status...   
1    [{'phone': 551194603981, 'status': 2, 'status_...   
2    [{'phone': 551195332832, 'status': 2, 'status_...   
3    [{'phone': 551194603981, 'status': 2, 'status_...   
4    [{'phone': 551195332832, 'status': 2, 'status_...   
..                                                 ...   
223  [{'phone': 5515992618875, 'status': 0, 'status...   
224  [{'phone': 5515992618875, 'status': 12, 'statu...   
225  [{'phone': 5515992618875, 'status': 0, 'status...   
226  [{'phone': 5515992618875, 'status': 0, 'status...   
227  [{'phone': 15992618875, 'status': 0, 'status_e...   

     task_phones_info_count  count_Delivered  count_Not delivered  \
0                         4                4                    0   
1                       483              412                   71   
2                       247              233                   14   
3                       359              345                   14   
4                       500              480                   20   
..                      ...              ...                  ...   
223                       1                0                    0   
224                       1                0                    1   
225                       1                0                    0   
226                       1                0                    0   
227                       1                0                    0   

     count_Ready to send  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  
..                   ...  
223                    1  
224                    0  
225                    1  
226                    1  
227                    1  

[228 rows x 13 columns]

In [ ]:
df_info_campanhas_contagem.to_csv('df_info_campanhas_contagem.csv', index=False)

In [ ]:
df_info_campanhas_contagem.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 13 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   result                  228 non-null    bool  
 1   id                      228 non-null    int64 
 2   address_book_id         228 non-null    int64 
 3   currency                228 non-null    object
 4   company_price           228 non-null    object
 5   send_date               228 non-null    object
 6   date_created            228 non-null    object
 7   sender_name             228 non-null    object
 8   task_phones_info        228 non-null    object
 9   task_phones_info_count  228 non-null    int64 
 10  count_Delivered         228 non-null    int64 
 11  count_Not delivered     228 non-null    int64 
 12  count_Ready to send     228 non-null    int64 
dtypes: bool(1), int64(6), object(6)
memory usage: 21.7+ KB


In [ ]:
# Renomear colunas em df_info_campanhas_contagem
df_info_campanhas_contagem = df_info_campanhas_contagem.rename(columns={
    'id' : 'id_campanhas',
    'send_date' : 'data_de_envio',
    'sender_name' : 'objetivo_campanha',
    'task_phones_info_count' : 'sms_enviados',
    'count_Delivered' : 'sms_entregue',
    'count_Not delivered' : 'sms_nao_entregue',
    'count_Ready to send' : 'sms_envios_pendentes'
})

display(df_info_campanhas_contagem)

result  id_campanhas  address_book_id currency company_price  \
0      True         29351                0      BRL       1.12000   
1      True         29382                0      BRL     135.24000   
2      True         29388                0      BRL      69.16000   
3      True         66958                0      BRL      75.39000   
4      True         66962                0      BRL     105.00000   
..      ...           ...              ...      ...           ...   
223    True       3477865                0      BRL       0.08000   
224    True       3477866                0      BRL       0.08000   
225    True       3477868                0      BRL       0.08000   
226    True       3477871                0      BRL       0.08000   
227    True       3477874                0      BRL       0.11000   

           data_de_envio         date_created objetivo_campanha  \
0    2021-11-17 13:31:22  2021-11-17 13:31:22           Ong BdM   
1    2021-11-17 13:46:19  2021-11-17 13:46:20           Ong BdM   
2    2021-11-17 13:48:49  2021-11-17 13:48:49           Ong BdM   
3    2021-12-08 14:26:01  2021-12-08 14:26:02           Ong BdM   
4    2021-12-08 14:28:27  2021-12-08 14:28:29           Ong BdM   
..                   ...                  ...               ...   
223  2024-10-03 20:57:05  2024-10-03 20:57:05           Somando   
224  2024-10-03 21:00:31  2024-10-03 21:00:31           Somando   
225  2024-10-03 21:11:07  2024-10-03 21:11:07           Somando   
226  2024-10-03 21:27:18  2024-10-03 21:27:18           Somando   
227  2024-10-03 21:31:30  2024-10-03 21:31:30           Somando   

                                      task_phones_info  sms_enviados  \
0    [{'phone': 5511959803214, 'status': 2, 'status...             4   
1    [{'phone': 551194603981, 'status': 2, 'status_...           483   
2    [{'phone': 551195332832, 'status': 2, 'status_...           247   
3    [{'phone': 551194603981, 'status': 2, 'status_...           359   
4    [{'phone': 551195332832, 'status': 2, 'status_...           500   
..                                                 ...           ...   
223  [{'phone': 5515992618875, 'status': 0, 'status...             1   
224  [{'phone': 5515992618875, 'status': 12, 'statu...             1   
225  [{'phone': 5515992618875, 'status': 0, 'status...             1   
226  [{'phone': 5515992618875, 'status': 0, 'status...             1   
227  [{'phone': 15992618875, 'status': 0, 'status_e...             1   

     sms_entregue  sms_nao_entregue  sms_envios_pendentes  
0               4                 0                     0  
1             412                71                     0  
2             233                14                     0  
3             345                14                     0  
4             480                20                     0  
..            ...               ...                   ...  
223             0                 0                     1  
224             0                 1                     0  
225             0                 0                     1  
226             0                 0                     1  
227             0                 0                     1  

[228 rows x 13 columns]

In [ ]:
df_info_campanhas_contagem.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 13 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   result                228 non-null    bool  
 1   id_campanhas          228 non-null    int64 
 2   address_book_id       228 non-null    int64 
 3   currency              228 non-null    object
 4   company_price         228 non-null    object
 5   data_de_envio         228 non-null    object
 6   date_created          228 non-null    object
 7   objetivo_campanha     228 non-null    object
 8   task_phones_info      228 non-null    object
 9   sms_enviados          228 non-null    int64 
 10  sms_entregue          228 non-null    int64 
 11  sms_nao_entregue      228 non-null    int64 
 12  sms_envios_pendentes  228 non-null    int64 
dtypes: bool(1), int64(6), object(6)
memory usage: 21.7+ KB


In [ ]:
df_campanhas_sms = df_info_campanhas_contagem[['id_campanhas','data_de_envio','objetivo_campanha','sms_enviados','sms_entregue','sms_nao_entregue','sms_envios_pendentes']]

In [ ]:
df_campanhas_sms.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Data columns (total 7 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   id_campanhas          228 non-null    int64 
 1   data_de_envio         228 non-null    object
 2   objetivo_campanha     228 non-null    object
 3   sms_enviados          228 non-null    int64 
 4   sms_entregue          228 non-null    int64 
 5   sms_nao_entregue      228 non-null    int64 
 6   sms_envios_pendentes  228 non-null    int64 
dtypes: int64(5), object(2)
memory usage: 12.6+ KB


In [ ]:
df_info_campanhas.head()

result     id  address_book_id currency company_price            send_date  \
0    True  29351                0      BRL       1.12000  2021-11-17 13:31:22   
1    True  29382                0      BRL     135.24000  2021-11-17 13:46:19   
2    True  29388                0      BRL      69.16000  2021-11-17 13:48:49   
3    True  66958                0      BRL      75.39000  2021-12-08 14:26:01   
4    True  66962                0      BRL     105.00000  2021-12-08 14:28:27   

          date_created sender_name  \
0  2021-11-17 13:31:22     Ong BdM   
1  2021-11-17 13:46:20     Ong BdM   
2  2021-11-17 13:48:49     Ong BdM   
3  2021-12-08 14:26:02     Ong BdM   
4  2021-12-08 14:28:29     Ong BdM   

                                    task_phones_info  task_phones_info_count  \
0  [{'phone': 5511959803214, 'status': 2, 'status...                       4   
1  [{'phone': 551194603981, 'status': 2, 'status_...                     483   
2  [{'phone': 551195332832, 'status': 2, 'status_...                     247   
3  [{'phone': 551194603981, 'status': 2, 'status_...                     359   
4  [{'phone': 551195332832, 'status': 2, 'status_...                     500   

                            explain_counts  count_Delivered  \
0                         {'Delivered': 4}                4   
1  {'Delivered': 412, 'Not delivered': 71}              412   
2  {'Delivered': 233, 'Not delivered': 14}              233   
3  {'Delivered': 345, 'Not delivered': 14}              345   
4  {'Delivered': 480, 'Not delivered': 20}              480   

   count_Not delivered  count_Ready to send  
0                    0                    0  
1                   71                    0  
2                   14                    0  
3                   14                    0  
4                   20                    0

In [ ]:
df_info_campanhas.to_csv('df_info_campanhas.csv', index=False)

In [ ]:
df_campanhas_sms.to_csv('df_campanhas_sms.csv', index=False)